# Strands Agent Deployment in Bedrock AgentCore Runtime

This workshop demonstrates how to deploy Strands Agents with Amazon Bedrock AgentCore Runtime, integrating multiple tools including MCP servers, code interpreters, and custom functions for comprehensive AI agent capabilities.

## Overview

In this lab, you will:
- Deploy a Strands Agent with multiple integrated tools
- Use MCP servers from previous labs as agent tools
- Integrate Bedrock AgentCore Code Interpreter
- Test the deployed agent with various scenarios
- Learn about observability and monitoring

## Prerequisites

Before starting this lab, ensure you have:
- Completed Lab 3 (EXA API Key stored in AgentCore Identity) and Lab 4 (MCP Server deployment)
- AWS credentials configured (IAM role or environment variables)
- Required Python packages installed
- Basic understanding of Strands Agents and Bedrock AgentCore concepts

If you're not running in an environment with an IAM role assumed, set your AWS credentials as environment variables:

In [ ]:
import os

#os.environ["AWS_ACCESS_KEY_ID"]=<YOUR ACCESS KEY>
#os.environ["AWS_SECRET_ACCESS_KEY"]=<YOUR SECRET KEY>
#os.environ["AWS_SESSION_TOKEN"]=<OPTIONAL - YOUR SESSION TOKEN IF TEMP CREDENTIAL>
#os.environ["AWS_REGION"]=<AWS REGION WITH BEDROCK AGENTCORE AVAILABLE>

Install required packages for Strands Agents, MCP integration, and Bedrock AgentCore SDK:

In [2]:
%pip install -q strands-agents strands-agents-tools bedrock-agentcore bedrock-agentcore-starter-toolkit

Note: you may need to restart the kernel to use updated packages.


## What is Strands Agent with Bedrock AgentCore Runtime?

Strands Agents provide a powerful framework for building AI agents with multiple tool integrations. When deployed with Bedrock AgentCore Runtime, you get:

- **Scalable Deployment**: Managed infrastructure with auto-scaling capabilities
- **Secure Authentication**: Built-in security with Cognito integration
- **Observability**: CloudWatch integration for monitoring and debugging
- **Multi-Tool Integration**: Combine MCP servers in AgentCore Runtime, Code Interpreters, and Browser

This lab demonstrates creating a comprehensive agent that can perform web searches, execute code, and handle custom business logic.

## Creating a Multi-Tool Strands Agent

Let's create a Strands Agent that integrates multiple tools from previous labs:

### Tool Integration Overview:
- **Custom Weather Tool**: Simple demonstration function
- **Calculator Tool**: Mathematical operations
- **Code Interpreter**: Execute Python code securely (Lab 1)
- **EXA MCP Tools**: Web search from remote MCP server (Lab 3)
- **Deployed MCP Tools**: Web search from AgentCore Runtime MCP server (Lab 4)

### Retrieve Configuration from Lab 3 and 4 for MCP Server connection

Load the MCP server deployment details and authentication configuration from the previous lab.

Components Retrieved:
- **Cognito Client ID**: For authentication with deployed MCP server
- **Cognito Pool ID**: User pool configuration
- **MCP Runtime ARN**: Deployed MCP server endpoint
- **MCP Runtime ID**: Runtime identifier
- **ECR Repository Name**: Container registry information

In [ ]:
# Lab 3: Check Bedrock AgentCore Identity for securely storing EXA API Key in Lab 3, or create if not exist
from bedrock_agentcore.services.identity import IdentityClient
import boto3

# !-------- UPDATE THE EXA API KEY HERE  --------!
EXA_API_KEY = <YOUR EXA API KEY> 

region = boto3.session.Session().region_name

#Configure API Key Provider
identity_client = IdentityClient(region=region)

try:
    api_key_provider = identity_client.create_api_key_credential_provider({
        "name": "exa-apikey-provider",
        "apiKey": EXA_API_KEY # Replace it with the API key you obtain from the external application vendor, e.g., OpenAI
    })
    print("Created AgentCore Identity API Key Credential Provider.")
except Exception as e:
    print("AgentCore Identity API Key Credential Provider already exist.")

Created AgentCore Identity API Key Credential Provider.


In [ ]:
# Lab 4: Retrieve and copy the configuration values to Strands Agents setup below for deployed MCP Server connection

%store -r cognito_client_id
%store -r cognito_pool_id
%store -r mcp_runtime_arn
%store -r mcp_runtime_id
%store -r mcp_ecr_repo_name

print(f"MCP Server AgentCore Runtime ARN: {mcp_runtime_arn}")
print(f"Cognito Client ID: {cognito_client_id}")

⚠️ **Note**: Update the MCP_RUNTIME_ARN and COGNITO_CLIENT_ID variables with values from your Lab 4 deployment.

In [ ]:
from strands import Agent, tool
from strands_tools import calculator
from strands_tools.code_interpreter import AgentCoreCodeInterpreter
from bedrock_agentcore.identity.auth import requires_api_key
from strands.tools.mcp import MCPClient
from mcp.client.streamable_http import streamablehttp_client
import boto3

# !-------- UPDATE THE CONFIGURATION VALUES FROM LAB 4  --------!
MCP_RUNTIME_ARN = <COPY MCP_RUNTIME_ARN IN LAB 4 HERE>
COGNITO_CLIENT_ID = <COPY COGNITO_CLIENT_ID IN LAB 4 HERE>

# Lab 0: Strands Agents Custom Tool
# -----------------------------------------
@tool
def weather(city: str) -> str:
    """Get weather information for a city
    Args:
        city: City or location name
    """
    return f"Weather for {city}: Sunny, 35°C" # dummy result for demo purpose


# Lab 1: Bedrock AgentCore Code Interpreter
# -----------------------------------------
print("Setting up Code Interpreter...")
agentcore_code_interpreter = AgentCoreCodeInterpreter()


# Lab 3: Bedrock AgentCore Identity - Secure API key for Remote MCP Server
# ------------------------------------------------------------------------
@requires_api_key(provider_name="exa-apikey-provider")
def need_api_key(*, api_key: str):
    #global EXA_API_KEY
    print(f'received api key for async func: {api_key}')
    return api_key
EXA_API_KEY = need_api_key()

# Connect to the EXA MCP server
exa_server = MCPClient(lambda: streamablehttp_client(f"https://mcp.exa.ai/mcp?exaApiKey={EXA_API_KEY}"))


# Lab 4: Bedrock AgentCore Runtime - MCP Server Hosting
# -----------------------------------------------------
print("Setting up MCP server authentication...")

region = boto3.session.Session().region_name
cognito_client = boto3.client('cognito-idp', region_name=region)

# Get bearer token (access token) from Cognito Auth 
auth_response = cognito_client.initiate_auth(
    ClientId=COGNITO_CLIENT_ID,
    AuthFlow='USER_PASSWORD_AUTH',
    AuthParameters={
        'USERNAME': 'testuser',
        'PASSWORD': 'MyPassword123!'
    }
)
bearer_token = auth_response['AuthenticationResult']['AccessToken']

# Configure deployed MCP server connection
encoded_arn = MCP_RUNTIME_ARN.replace(':', '%3A').replace('/', '%2F')
mcp_url = f"https://bedrock-agentcore.{region}.amazonaws.com/runtimes/{encoded_arn}/invocations?qualifier=DEFAULT"
headers = {"Authorization": f"Bearer {bearer_token}"}

# Connect to the deployed MCP server
print("Connecting to MCP server...")
websearch_server = MCPClient(lambda: streamablehttp_client(mcp_url, headers))


# Create and test the comprehensive Strands Agent
with exa_server, websearch_server:
    mcp_tools = (exa_server.list_tools_sync() + websearch_server.list_tools_sync())
    print(f"Available MCP tools: {[tool.tool_name for tool in mcp_tools]}")

    agent = Agent(
        model="us.amazon.nova-pro-v1:0",
        system_prompt = """You are a helpful assistant that provides concise responses.
                        If web search, always use websearch tool first.
                        Use code generation to solve more complex logic tasks.
                        """,
        tools=[weather, calculator, agentcore_code_interpreter.code_interpreter] + mcp_tools,
    )

    print("\n=== Testing Agent Capabilities ===")
    print("\n1. Testing custom weather tool:")
    agent("How is the weather in HK?")
    
    print("\n2. Testing calculator tool:")
    agent("2+2=")
    
    print("\n3. Testing web search via MCP:")
    agent("What is Bedrock AgentCore?")
    
    print("\n4. Testing code interpreter:")
    agent("Tell me the largest random prime number between 1 and 100, which is less than 84 and more that 9")

Setting up Code Interpreter...
Found existing workload identity from /Users/heichow/Workspaces/bedrock-agentcore-workshop/05-bedrock-agentcore-runtime-strands/.agentcore.json: workload-ed777e3b
Found existing user id from /Users/heichow/Workspaces/bedrock-agentcore-workshop/05-bedrock-agentcore-runtime-strands/.agentcore.json: 17006071
received api key for async func: 5f9cf60b-c56a-433b-9574-544da3aa1efb
Setting up MCP server authentication...
Connecting to MCP server...
Available MCP tools: ['web_search_exa', 'company_research_exa', 'crawling_exa', 'linkedin_search_exa', 'deep_researcher_start', 'deep_researcher_check', 'websearch']

=== Testing Agent Capabilities ===

1. Testing custom weather tool:
我可以为您查询香港的天气情况。让我现在获取最新的天气信息。
Tool #1: weather
根据最新信息，香港目前天气状况为晴朗，气温为35°C(摄氏度)。天气相当炎热，如果您在香港或计划前往，建议做好防晒和补充水分的准备。
2. Testing calculator tool:
这是一个简单的数学运算。让我为您计算2+2的结果。
Tool #2: calculator


╭────────────────────────────────────────────── Calculation Result ───────────────────────────────────────────────╮
│                                                                                                                 │
│  ╭───────────┬─────────────────────╮                                                                            │
│  │ Operation │ Evaluate Expression │                                                                            │
│  │ Input     │ 2+2                 │                                                                            │
│  │ Result    │ 4                   │                                                                            │
│  ╰───────────┴─────────────────────╯                                                                            │
│                                                                                                                 │
╰─────────────────────────────────────────────────────────────────────────────────────────────────────────────────╯

2+2=4
3. Testing web search via MCP:
我需要在网络上搜索关于Amazon上的咖啡机信息。让我为您搜索这些信息。
Tool #3: websearch
现在我需要查询Amazon上特定的咖啡机详细信息。让我搜索Amazon咖啡机产品页面。
Tool #4: websearch
让我直接查询Amazon咖啡机畅销榜的第一款产品信息。
Tool #5: crawling_exa
我注意到无法通过直接爬取获取Amazon畅销榜页面的详细内容。让我尝试搜索最新的Amazon咖啡机畅销信息。
Tool #6: websearch
现在我需要尝试获取Amazon上具体咖啡机产品的详细信息。让我搜索Cuisinart DCC-3200P1咖啡机，它似乎是畅销款之一。
Tool #7: crawling_exa
我尝试了几种方法来获取Amazon上畅销咖啡机的详细信息，但直接获取完整信息有些困难。让我基于搜索结果整理出关于Cuisinart DCC-3200P1(看起来是最畅销的咖啡机之一)的信息：
Tool #8: websearch
现在我已经收集了足够的信息，我将为您提供Amazon上畅销咖啡机Cuisinart DCC-3200P1的详细信息：

## Cuisinart DCC-3200P1 14杯可编程咖啡机详细信息

**产品名称：** Cuisinart DCC-3200P1 PerfecTemp 14杯可编程咖啡机

**主要特点：**
1. **容量：** 14杯大容量玻璃壶
2. **温度技术：** 采用前沿咖啡技术，提供更热的咖啡而不牺牲口味
3. **咖啡浓度控制：** 可选择常规或浓烈口味
4. **可编程功能：** 24小时可预设煮制时间
5. **特殊设置：** 1-4杯小容量煮制设置
6. **控制面板：** 带背光的LCD显示屏，操作简便
7. **自动关闭功能：** 可调节自动关闭时间
8. **温度控制：** 可调节保温板温度(低、中、高)以保持咖啡温度
9. **暂停功能：** 中途可暂停取杯
10. **自清洁功能：** 内置除钙提示灯和自清洁系统
11. **声音提示：** 可开启或关闭就绪提示音

**产品规格：**
- 尺寸：7.75英寸长 × 9英寸宽 × 14英寸高
- 重量：9.2磅(约4.1

╭─────────────────────────────────────────────── Calculation Error ───────────────────────────────────────────────╮
│                                                                                                                 │
│  Error: Invalid expression: Logical operators are not supported in mathematical expressions                     │
│                                                                                                                 │
╰─────────────────────────────────────────────────────────────────────────────────────────────────────────────────╯

我需要使用不同的方法来解决这个问题。让我用代码解决。
Tool #10: code_interpreter
现在我会编写代码来找出大于9且小于84的最大素数：
Tool #11: code_interpreter
我已经找到答案了。大于9且小于84的最大素数是83。

计算过程说明：
1. 我编写了一个程序来检查每个数字是否为素数
2. 然后从83开始向下检查，直到找到第一个素数
3. 结果显示83本身就是一个素数

素数的定义是只能被1和它自身整除的大于1的整数。83符合这个条件，它不能被任何小于它的数(除了1)整除。

所以，1到100之间，大于9且小于84的最大素数是83。

Session termination failed: 404


## Deploy Strands Agent to Bedrock AgentCore Runtime

Create a deployable version of our Strands Agent and deploy it as a managed service.
![bedrock-agentcore-runtime-launch](images/runtime-launch.png)

### Deployment Process:
1. Create Python file with agent configuration
2. Set up requirements.txt with dependencies
3. Configure AgentCore Runtime with authentication
4. Deploy using CodeBuild for containerization

### Step 1: Create Python File with Agent Configuration

Create the main Python file that defines our Strands Agent with all integrated tools. This file will be deployed to Bedrock AgentCore Runtime as a containerized service.

**Deployment Requirements:**
To deploy agents to AgentCore Runtime, we need to:
- Import the Runtime App: `from bedrock_agentcore.runtime import BedrockAgentCoreApp`
- Initialize the App: `app = BedrockAgentCoreApp()`
- Decorate the invocation function with `@app.entrypoint`
- Let AgentCore Runtime control execution with `app.run()`

In [17]:
# Copy the values in Lab 4 to Strands Agents setup below
print(f"MCP Server AgentCore Runtime ARN: {mcp_runtime_arn}")
print(f"Cognito Client ID: {cognito_client_id}")

MCP Server AgentCore Runtime ARN: arn:aws:bedrock-agentcore:us-east-1:960268301246:runtime/mcp_server_agentcore-4gapoe8BMl
Cognito Client ID: 21p07oeqcuq5n3ufkc5u2q9fs


⚠️ **Note**: Update the MCP_RUNTIME_ARN and COGNITO_CLIENT_ID variables with values from your Lab 4 deployment.

In [ ]:
%%writefile strands_agent.py
from strands import Agent, tool
from strands_tools import calculator
from strands_tools.code_interpreter import AgentCoreCodeInterpreter
from strands.tools.mcp import MCPClient
from mcp.client.streamable_http import streamablehttp_client
import boto3
from bedrock_agentcore.runtime import BedrockAgentCoreApp

app = BedrockAgentCoreApp()

# !-------- UPDATE THE CONFIGURATION VALUES FROM LAB 4  --------!
MCP_RUNTIME_ARN = <COPY MCP_RUNTIME_ARN IN LAB 4 HERE>
COGNITO_CLIENT_ID = <COPY COGNITO_CLIENT_ID IN LAB 4 HERE>

# Lab 0: Strands Agents Custom Tool
# -----------------------------------------
@tool
def weather(city: str) -> str:
    """Get weather information for a city
    Args:
        city: City or location name
    """
    return f"Weather for {city}: Sunny, 35°C"


# Lab 1: Bedrock AgentCore Code Interpreter
# -----------------------------------------
print("Setting up Code Interpreter...")
agentcore_code_interpreter = AgentCoreCodeInterpreter()


# Lab 3: Bedrock AgentCore Identity - Secure API key for Remote MCP Server
# ------------------------------------------------------------------------
# Issue exists when retrieving API key in AgentCore Runtime, comment out first
'''
@requires_api_key(provider_name="exa-apikey-provider")
def need_api_key(*, api_key: str):
    #global EXA_API_KEY
    print(f'received api key for async func: {api_key}')
    return api_key
EXA_API_KEY = need_api_key()

# Connect to the EXA MCP server
exa_server = MCPClient(lambda: streamablehttp_client(f"https://mcp.exa.ai/mcp?exaApiKey={EXA_API_KEY}"))
'''

# Lab 4: Bedrock AgentCore Runtime - MCP Server Hosting
# -----------------------------------------------------
print("Setting up MCP server authentication...")

region = boto3.session.Session().region_name
cognito_client = boto3.client('cognito-idp', region_name=region)

# Get bearer token (access token) from Cognito Auth 
auth_response = cognito_client.initiate_auth(
    ClientId=COGNITO_CLIENT_ID,
    AuthFlow='USER_PASSWORD_AUTH',
    AuthParameters={
        'USERNAME': 'testuser',
        'PASSWORD': 'MyPassword123!'
    }
)
bearer_token = auth_response['AuthenticationResult']['AccessToken']

# Configure deployed MCP server connection
encoded_arn = MCP_RUNTIME_ARN.replace(':', '%3A').replace('/', '%2F')
mcp_url = f"https://bedrock-agentcore.{region}.amazonaws.com/runtimes/{encoded_arn}/invocations?qualifier=DEFAULT"
headers = {"Authorization": f"Bearer {bearer_token}"}

# Connect to the deployed MCP server
print("Connecting to MCP server...")
websearch_server = MCPClient(lambda: streamablehttp_client(mcp_url, headers))


# Create and test the comprehensive Strands Agent
#with exa_server, websearch_server:
#    mcp_tools = (exa_server.list_tools_sync() + websearch_server.list_tools_sync())
with websearch_server:
    mcp_tools = (websearch_server.list_tools_sync())
    print(f"Available MCP tools: {[tool.tool_name for tool in mcp_tools]}")
    agent = Agent(
        model="us.amazon.nova-pro-v1:0",
        system_prompt = """You are a helpful assistant that provides concise responses.
                        If web search, always use websearch tool first.
                        Use code generation to solve more complex logic tasks.
                        """,
        tools=[weather, calculator, agentcore_code_interpreter.code_interpreter] + mcp_tools,
    )

@app.entrypoint
async def strands_agent_bedrock(payload, context):
    """
    Invoke the agent with a payload
    """
    print(f"Payload: {payload}")
    print(f"Context: {context}")
    user_input = payload.get("prompt", "No prompt found")
    stream = agent.stream_async(user_input)
    async for event in stream:
        if "data" in event:
            yield event
    print(agent.messages)

if __name__ == "__main__":
    app.run()

Overwriting strands_agent.py


## What happens behind the scenes?

When you use `BedrockAgentCoreApp`, it automatically:

* Creates an HTTP server that listens on the port 8080
* Implements the required `/invocations` endpoint for processing the agent's requirements
* Implements the `/ping` endpoint for health checks (very important for asynchronous agents)
* Handles proper content types and response formats
* Manages error handling according to the AWS standards

### Local Testing (Optional)

Before deploying to AgentCore Runtime, you can test the agent locally to verify functionality.

**Start Local Server:**
```bash
uv run strands_agent.py
```
or
```bash
python strands_agent.py
```
The server will start at `http://localhost:8080`

**Test with cURL:**
```bash
curl -X POST http://localhost:8080/invocations \
  -H "Content-Type: application/json" \
  -H "X-Amzn-Bedrock-AgentCore-Runtime-User-Id: 123" \
  -H "X-Amzn-Bedrock-AgentCore-Runtime-Session-Id: 1234567890123456789012345678901234567890" \
  -d '{"prompt": "How is the weather in HK?"}'
```

### Step 2: Create Requirements File

Define the Python dependencies needed for our Strands Agent deployment.

**Key Dependencies:**
- **aws-opentelemetry-distro**: Required for AgentCore observability
- **strands-agents**: Core Strands framework
- **bedrock-agentcore**: Runtime integration

**Observability Integration:**
The `aws-opentelemetry-distro` library enables automatic instrumentation for monitoring and tracing. As documented in the [AgentCore Observability Guide](https://docs.aws.amazon.com/bedrock-agentcore/latest/devguide/observability-configure.html), the containerized environment (such as docker) need to add the following command:

```dockerfile
CMD ["opentelemetry-instrument", "python", "main.py"]
```

This auto-instrumentation approach automatically adds the OpenTelemetry SDK to the Python path for comprehensive observability.

In [20]:
%%writefile requirements.txt
strands-agents
strands-agents-tools
bedrock-agentcore
bedrock-agentcore-starter-toolkit
boto3
aws-opentelemetry-distro>=0.10.0

Overwriting requirements.txt


### Observability Setup (Optional)

**CloudWatch APM Configuration:**
Enable CloudWatch APM → Transaction Search for comprehensive observability and monitoring of your deployed Strands Agent. In this lab, set X-Ray trace indexing to 100% for generating all trace summaries for end-to-end transaction analytics.
![bedrock-agentcore-observability-setup](images/observability-setup.png)

**Benefits:**
- **Performance Monitoring**: Request tracing and response time metrics
- **Error Tracking**: Comprehensive debugging capabilities
- **Usage Analytics**: Patterns and usage insights
- **Distributed Tracing**: End-to-end request flow visibility

### Step 3: Configure AgentCore Runtime

Set up the Bedrock AgentCore Runtime configuration with automatic resource creation.

**Generated Artifacts:**
This step creates essential deployment files:
- **Dockerfile**: Container configuration for the Strands Agent
- **.dockerignore**: list the excluded files when docker build
- **.bedrock_agentcore.yaml**: Runtime deployment configuration

Please note that when using the bedrock_agentcore_starter_toolkit to configure your agent, it takes care of the opentelemetry instrumentation. The generated Dockerfile will include:
```bash
CMD ["opentelemetry-instrument", "python", "runtime_agent_main.py"]
```

In [29]:
from bedrock_agentcore_starter_toolkit import Runtime
import boto3

region = boto3.session.Session().region_name
agentcore_runtime = Runtime()

response = agentcore_runtime.configure(
    entrypoint="strands_agent.py",
    auto_create_execution_role=True,
    auto_create_ecr=True,
    requirements_file="requirements.txt",
    region=region,
    agent_name="strands_claude_getting_started"
)
response

Entrypoint parsed: file=/Users/heichow/Workspaces/bedrock-agentcore-workshop/05-bedrock-agentcore-runtime-strands/strands_agent.py, bedrock_agentcore_name=strands_agent
Configuring BedrockAgentCore agent: strands_claude_getting_started


⚠️  ℹ️  No container engine found (Docker/Finch/Podman not installed)
✅ Default deployment uses CodeBuild (no container engine needed)
💡 Run 'agentcore launch' for cloud-based building and deployment
💡 For local builds, install Docker, Finch, or Podman

Generated Dockerfile: /Users/heichow/Workspaces/bedrock-agentcore-workshop/05-bedrock-agentcore-runtime-strands/Dockerfile
Generated .dockerignore: /Users/heichow/Workspaces/bedrock-agentcore-workshop/05-bedrock-agentcore-runtime-strands/.dockerignore
Keeping 'strands_claude_getting_started' as default agent
Bedrock AgentCore configured: /Users/heichow/Workspaces/bedrock-agentcore-workshop/05-bedrock-agentcore-runtime-strands/.bedrock_agentcore.yaml


ConfigureResult(config_path=PosixPath('/Users/heichow/Workspaces/bedrock-agentcore-workshop/05-bedrock-agentcore-runtime-strands/.bedrock_agentcore.yaml'), dockerfile_path=PosixPath('/Users/heichow/Workspaces/bedrock-agentcore-workshop/05-bedrock-agentcore-runtime-strands/Dockerfile'), dockerignore_path=PosixPath('/Users/heichow/Workspaces/bedrock-agentcore-workshop/05-bedrock-agentcore-runtime-strands/.dockerignore'), runtime='None', region='us-east-1', account_id='960268301246', execution_role=None, ecr_repository=None, auto_create_ecr=True)

### Step 4: Deploy to AgentCore Runtime

Launch the deployment process using AWS CodeBuild for containerization and deployment.

**Deployment Process:**
- Builds a containerized version of your Strands Agents
- Creates required AWS resources (ECR repository, IAM roles)
- Push container image to Amazon ECR
- Deploys to AgentCore Runtime as a managed, auto-scaling service

In [30]:
launch_result = agentcore_runtime.launch()

🚀 CodeBuild mode: building in cloud (RECOMMENDED - DEFAULT)
   • Build ARM64 containers in the cloud with CodeBuild
   • No local Docker required
💡 Available deployment modes:
   • runtime.launch()                           → CodeBuild (current)
   • runtime.launch(local=True)                 → Local development
   • runtime.launch(local_build=True)           → Local build + cloud deploy (NEW)
Starting CodeBuild ARM64 deployment for agent 'strands_claude_getting_started' to account 960268301246 (us-east-1)
Starting CodeBuild ARM64 deployment for agent 'strands_claude_getting_started' to account 960268301246 (us-east-1)
Setting up AWS resources (ECR repository, execution roles)...
Getting or creating ECR repository for agent: strands_claude_getting_started
✅ ECR repository available: 960268301246.dkr.ecr.us-east-1.amazonaws.com/bedrock-agentcore-strands_claude_getting_started
Getting or creating execution role for agent: strands_claude_getting_started
Using AWS region: us-east-1, accoun

✅ Reusing existing ECR repository: 960268301246.dkr.ecr.us-east-1.amazonaws.com/bedrock-agentcore-strands_claude_getting_started


✅ Reusing existing execution role: arn:aws:iam::960268301246:role/AmazonBedrockAgentCoreSDKRuntime-us-east-1-8556fc4504
✅ Execution role available: arn:aws:iam::960268301246:role/AmazonBedrockAgentCoreSDKRuntime-us-east-1-8556fc4504
Preparing CodeBuild project and uploading source...
Getting or creating CodeBuild execution role for agent: strands_claude_getting_started
Role name: AmazonBedrockAgentCoreSDKCodeBuild-us-east-1-8556fc4504
Reusing existing CodeBuild execution role: arn:aws:iam::960268301246:role/AmazonBedrockAgentCoreSDKCodeBuild-us-east-1-8556fc4504
Using .dockerignore with 44 patterns
Uploaded source to S3: strands_claude_getting_started/20250814-213447.zip
Updated CodeBuild project: bedrock-agentcore-strands_claude_getting_started-builder
Starting CodeBuild build (this may take several minutes)...
Starting CodeBuild monitoring...
🔄 QUEUED started (total: 0s)
✅ QUEUED completed in 5.3s
🔄 PROVISIONING started (total: 6s)
✅ PROVISIONING completed in 5.3s
🔄 DOWNLOAD_SOURCE s

### Step 5: Verify Deployment Status

Monitor the deployment progress and wait for the runtime to be ready:

In [ ]:
import time

print("Checking AgentCore Runtime status...")
status_response = agentcore_runtime.status()
status = status_response.endpoint['status']
print(f"Initial status: {status}")

end_status = ['READY', 'CREATE_FAILED', 'DELETE_FAILED', 'UPDATE_FAILED']
while status not in end_status:
    print(f"Status: {status} - waiting...")
    time.sleep(10)
    status_response = agentcore_runtime.status()
    status = status_response.endpoint['status']

if status == 'READY':
    print("✓ AgentCore Runtime is READY!")
else:
    print(f"⚠ AgentCore Runtime status: {status}")
    
print(f"Final status: {status}")

strands_runtime_id = launch_result.agent_id
strands_runtime_arn = launch_result.agent_arn
strands_ecr_repo_name = launch_result.ecr_uri.split('/')[1]
print(f"Strands AgentCore Runtime ID: {strands_runtime_id}")
print(f"Strands AgentCore Runtime ARN: {strands_runtime_arn}")
print(f"ECR Repo for Strands AgentCore Runtime: {strands_ecr_repo_name}")

Checking AgentCore Runtime status...


Retrieved Bedrock AgentCore status for: strands_claude_getting_started


Initial status: READY
✓ AgentCore Runtime is READY!
Final status: READY


## Testing the Deployed Agent

Test the deployed Strands Agent by invoking it through the Bedrock AgentCore Runtime API with various prompts to verify all integrated tools are working correctly.

In [ ]:
import boto3
import json
import uuid

PROMPT = "How is the weather in HK?"

agent_runtime_arn = launch_result.agent_arn
session_id = str(uuid.uuid4())

agentcore_client = boto3.client(
    'bedrock-agentcore',
    region_name=boto3.session.Session().region_name
)

boto3_response = agentcore_client.invoke_agent_runtime(
    agentRuntimeArn=agent_runtime_arn,
    qualifier="DEFAULT",
    runtimeUserId="123",
    runtimeSessionId=session_id, #Provide same session identifier across multiple requests to maintain conversation context, and with better traceability
    payload=json.dumps({"prompt": PROMPT})
)

if "text/event-stream" in boto3_response.get("contentType", ""):
    for line in boto3_response["response"].iter_lines(chunk_size=1):
        if line:
            line = line.decode("utf-8")
            if line.startswith("data: "):
                print(line)
else:
    events = []
    for event in boto3_response.get("response", []):
        events.append(event)

data: "{'data': '我', 'delta': {'text': '我'}, 'agent': <strands.agent.agent.Agent object at 0xffff78e9fdd0>, 'event_loop_cycle_id': UUID('90901c36-a515-4db6-a57f-1c86aa0cb995'), 'request_state': {}, 'event_loop_cycle_trace': <strands.telemetry.metrics.Trace object at 0xffff6eb985f0>, 'event_loop_cycle_span': _Span(name=\"execute_event_loop_cycle\", context=SpanContext(trace_id=0x689e574c8cce0d460f039066304b9cba, span_id=0x89d6db1eff69f16a, trace_flags=0x01, trace_state=[], is_remote=False))}"
data: "{'data': '很樂意', 'delta': {'text': '很樂意'}, 'agent': <strands.agent.agent.Agent object at 0xffff78e9fdd0>, 'event_loop_cycle_id': UUID('90901c36-a515-4db6-a57f-1c86aa0cb995'), 'request_state': {}, 'event_loop_cycle_trace': <strands.telemetry.metrics.Trace object at 0xffff6eb985f0>, 'event_loop_cycle_span': _Span(name=\"execute_event_loop_cycle\", context=SpanContext(trace_id=0x689e574c8cce0d460f039066304b9cba, span_id=0x89d6db1eff69f16a, trace_flags=0x01, trace_state=[], is_remote=False))}"
da

### Testing Conversation History

Verify that the agent maintains conversation context across multiple requests using the same session ID:

In [ ]:
PROMPT = "What did I ask?"

boto3_response = agentcore_client.invoke_agent_runtime(
    agentRuntimeArn=agent_runtime_arn,
    qualifier="DEFAULT",
    runtimeUserId="123",
    runtimeSessionId=session_id, #Provide same session identifier across multiple requests to maintain conversation context, and with better traceability
    payload=json.dumps({"prompt": PROMPT})
)

if "text/event-stream" in boto3_response.get("contentType", ""):
    for line in boto3_response["response"].iter_lines(chunk_size=1):
        if line:
            line = line.decode("utf-8")
            if line.startswith("data: "):
                print(line)
else:
    events = []
    for event in boto3_response.get("response", []):
        events.append(event)

data: "{'data': '很抱', 'delta': {'text': '很抱'}, 'agent': <strands.agent.agent.Agent object at 0xffff78e9fdd0>, 'event_loop_cycle_id': UUID('ad30ec14-a3ce-4244-94bb-7470361fd2f5'), 'request_state': {}, 'event_loop_cycle_trace': <strands.telemetry.metrics.Trace object at 0xffff6eb98c50>, 'event_loop_cycle_span': _Span(name=\"execute_event_loop_cycle\", context=SpanContext(trace_id=0x689e57c29f354edb6968510706c9b887, span_id=0x629adb6552781695, trace_flags=0x01, trace_state=[], is_remote=False))}"
data: "{'data': '歉，', 'delta': {'text': '歉，'}, 'agent': <strands.agent.agent.Agent object at 0xffff78e9fdd0>, 'event_loop_cycle_id': UUID('ad30ec14-a3ce-4244-94bb-7470361fd2f5'), 'request_state': {}, 'event_loop_cycle_trace': <strands.telemetry.metrics.Trace object at 0xffff6eb98c50>, 'event_loop_cycle_span': _Span(name=\"execute_event_loop_cycle\", context=SpanContext(trace_id=0x689e57c29f354edb6968510706c9b887, span_id=0x629adb6552781695, trace_flags=0x01, trace_state=[], is_remote=False))}"
da

## Conversation History and Session Management

**Strands Agents Conversation Management:**
Strands Agents includes built-in conversation management with a default `SlidingWindowConversationManager` strategy. This automatically maintains conversation context within sessions.

**Reference:** [Strands Agents Conversation Management](https://strandsagents.com/latest/documentation/docs/user-guide/concepts/agents/conversation-management/)

**AgentCore Runtime Session Isolation:**
- **Session Isolation**: Each user session is isolated and secure
- **Context Reuse**: Conversation history is maintained across multiple invocations
- **Session Duration**: Ephemeral sessions last up to 8 hours
- **Automatic Cleanup**: Sessions are automatically cleaned up after expiration

**Reference:** [AgentCore Runtime Sessions](https://docs.aws.amazon.com/bedrock-agentcore/latest/devguide/runtime-sessions.html)

**Long-term Memory:**
For persistent memory beyond session duration, integrate with Bedrock AgentCore Memory for long-term conversation storage and retrieval.

## AgentCore Observability on Amazon CloudWatch

### What is Bedrock AgentCore Observability?

Amazon Bedrock AgentCore provides built-in observability through CloudWatch and X-Ray integration. This enables monitoring of agent performance, tracing request flows, and analyzing conversation patterns.

Key features:
- **Session Tracking**: Monitor individual conversations
- **Distributed Tracing**: Track requests across components
- **Performance Metrics**: Latency, throughput, and error rates
- **Span Analysis**: Detailed execution breakdown

Learn more: [AgentCore Observability Guide](https://docs.aws.amazon.com/bedrock-agentcore/latest/devguide/observability.html)

### Viewing the Main Dashboard

Access the CloudWatch console to view your AgentCore observability dashboard:
![observability-main-dashboard.png](images/observability-main-dashboard.png)

### Session Management

Click **DEFAULT** in `strands_claude_getting_started` to view session history. This shows our test session with two traces: "香港的天气怎么样？" and "我问你什么了？"
![observability-session-list.png](images/observability-session-list.png)

### Session Overview

Select a session to see metrics, trace timeline, and performance data:
![observability-session-overview.png](images/observability-session-overview.png)

### Trace Analysis

Click any trace to examine detailed execution steps:

**Trace Summary**:
![observability-trace-summary.png](images/observability-trace-summary.png)

**Span Details**:
![observability-trace-span-1.png](images/observability-trace-span-1.png)
![observability-trace-span-2.png](images/observability-trace-span-2.png)

## Resource Cleanup (Optional)

⚠️ **Warning**: This will delete all resources created during the workshop. Only proceed if you no longer need the deployed agents.

**Resources to be cleaned up:**
- **Strands Agent Runtime**: The deployed multi-tool agent
- **MCP Server Runtime**: The web search MCP server from Lab 4
- **ECR Repositories**: Container images for both runtimes
- **Cognito User Pool**: Authentication infrastructure
- **AgentCore Identity**: API key provider from Lab 3

**Cleanup Process:**
The script will attempt to delete resources in the correct order to avoid dependency conflicts.

In [ ]:
import boto3
import os

agentcore_control_client = boto3.client('bedrock-agentcore-control', region_name=region)
ecr_client = boto3.client('ecr',region_name=region)
cognito_client = boto3.client('cognito-idp', region_name=region)

try:
    print("Deleting AgentCore Runtime for Strands...")
    agentcore_control_client.delete_agent_runtime(agentRuntimeId=strands_runtime_id)
    print("✓ AgentCore Runtime deletion initiated")

    print("Deleting ECR repository for Strands...")
    ecr_client.delete_repository(repositoryName=strands_ecr_repo_name, force=True)
    print("✓ ECR repository deleted")

    print("Deleting AgentCore Runtime for MCP...")
    agentcore_control_client.delete_agent_runtime(agentRuntimeId=mcp_runtime_id)
    print("✓ AgentCore Runtime deletion initiated")

    print("Deleting ECR repository for MCP...")
    ecr_client.delete_repository(repositoryName=mcp_ecr_repo_name, force=True)
    print("✓ ECR repository deleted")

    print("Deleting Cognito User Pool...")
    cognito_client.delete_user_pool(UserPoolId=cognito_pool_id)
    print("✓ Cognito User Pool deleted")

    print("Deleting AgentCore Identity...")
    agentcore_control_client.delete_api_key_credential_provider(name="exa-apikey-provider")
    print("✓ AgentCore Identity deletion initiated")

    print("Deleting Bedrock AgentCore configuration file for Strands...")
    os.remove(".bedrock_agentcore.yaml") 
    print("✓ .bedrock_agentcore.yaml deleted")

    print("Deleting Bedrock AgentCore configuration file for MCP...")
    os.remove("../04-bedrock-agentcore-runtime-mcp/.bedrock_agentcore.yaml") 
    print("✓ .bedrock_agentcore.yaml deleted")
except Exception as e:
    print(f"❌ Error during cleanup: {e}")
    print("You may need to manually clean up some resources.")

Deleting AgentCore Runtime for Strands...
✓ AgentCore Runtime deletion initiated
Deleting ECR repository for Strands...
✓ ECR repository deleted
Deleting AgentCore Runtime for MCP...
✓ AgentCore Runtime deletion initiated
Deleting ECR repository for MCP...
✓ ECR repository deleted
Deleting Cognito User Pool...
✓ Cognito User Pool deleted
Deleting AgentCore Identity...
✓ AgentCore Identity deletion initiated
